> Please go through Giba's post and kernel  to underrstand what this leak is all about
> https://www.kaggle.com/titericz/the-property-by-giba (kernel)
> https://www.kaggle.com/c/santander-value-prediction-challenge/discussion/61329 (post)
> 
> Also, go through this Jiazhen's kernel which finds more columns to exploit leak
> https://www.kaggle.com/johnfarrell/giba-s-property-extended-result
> 
> I just exploit data property in brute force way and then fill in remaining by row non zero means! This should bring everyone on level-playing field.
> 
> **Let the competition begin! :D**

### Just some small modifications from [original baseline](https://www.kaggle.com/tezdhar/breaking-lb-fresh-start)~
- The leak rows are calculated separately on train/test set
- Calculated the leaky values, correctness, for each lag
- Hope this can help to do some *lag_selection*

### Update leak process codes to Dmitry Frumkin's *fast* [version](https://www.kaggle.com/dfrumkin/a-simple-way-to-use-giba-s-features-v2)
- The result of Dmitry's original function and result of Hasan's function seem slightly different
- Modified to make the output consistent with Hasan's function (Seems better score)

In [1]:
import warnings
warnings.filterwarnings('ignore')
import gc

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import os
# print(os.listdir("../input"))

import lightgbm as lgb
from sklearn.model_selection import *
from sklearn.metrics import mean_squared_error, make_scorer
from scipy.stats import mode, skew, kurtosis, entropy
from sklearn.ensemble import ExtraTreesRegressor
from sklearn.metrics import mean_squared_error

import matplotlib.pyplot as plt
import seaborn as sns

import dask.dataframe as dd
from dask.multiprocessing import get

from tqdm import tqdm, tqdm_notebook
tqdm.pandas(tqdm_notebook)

# Any results you write to the current directory are saved as output.

In [2]:
train = pd.read_csv("train.csv")
test = pd.read_csv("test.csv")

transact_cols = [f for f in train.columns if f not in ["ID", "target"]]
y = np.log1p(train["target"]).values

In [3]:
test["target"] = train["target"].mean()

# Determine Extra Features to use

In [100]:
rows = [1757, 3809, 511, 3798, 625, 3303, 4095, 1283, 4209, 1696, 3511, 816, 245, 1383, 2071, 3492, 378, 2971, 2366, 4414, 2790, 3979, 193, 1189, 3516, 810, 4443, 3697, 235, 1382, 4384, 3418, 4396, 921, 3176, 650]

def element_wise_comparison(i1, i2, thresh=3):
    i1 = np.array(i1)
    i2 = np.array(i2)
    dif = i1 - i2
    count = np.count_nonzero(dif)
    if count <= thresh:
        return True
    else:
        return False

def solve_ties_in_nb_of_fillers(df, counts, stop_thresh=2):
    args = np.argsort(counts)[::-1]
    stop = np.squeeze(np.where(counts[args] == len(df.index)-stop_thresh))
    try:
        stop = int(stop)
    except:
          return [None]
    u, c = np.unique(counts[args[stop:]], return_counts=True)
    conflicts = u[np.where(c > 1)]
    for c in conflicts:
        idx = np.squeeze(np.where(counts == c))
        ref_id = np.squeeze(np.where(counts == c+1))
        ref = df.iloc[:-1, int(ref_id)]
        dif1 = np.count_nonzero(df.iloc[1:, idx[0]].values - ref.values)
        dif2 = np.count_nonzero(df.iloc[1:, idx[1]].values - ref.values)
        loc0  = np.where(args == idx[0])
        loc1  = np.where(args == idx[1])
        tmp0 = args[loc0]
        tmp1 = args[loc1]

        if dif2 < dif1:
            args[np.minimum(loc0, loc1)] = tmp1
            args[np.maximum(loc0, loc1)] = tmp0
        else:
            args[np.minimum(loc0, loc1)] = tmp0
            args[np.maximum(loc0, loc1)] = tmp1           

    return args[stop:]
    
        
def find_filler_value(df, idx):
    u, c = np.unique(df.iloc[0,:].values, return_counts=True)
    arg = np.argsort(c)
    return u[arg][-idx]

def find_col_order_by_filler(df, filler, stop_thresh=2, nb=40):
    counts = []
    for c in df.columns:
        v = df[c].values - filler
        counts.append(np.count_nonzero(v))
    counts = np.array(counts)
    args = solve_ties_in_nb_of_fillers(df, counts, stop_thresh)
    if not all(args):
        return [None]
    return df.iloc[:, args]

def find_leading_col(raw_df, sorted_df):
    curr_lead = sorted_df.apply(tuple, axis=0).to_frame().rename(columns={0: 'key'}).iloc[0, 0][1:]
    cols_to_match = raw_df.apply(tuple, axis=0).to_frame().rename(columns={0: 'key'})
    for c in cols_to_match.index:
        if element_wise_comparison(cols_to_match.loc[c, 'key'][:-1], curr_lead):
            print('Leading col found: {}'.format(c))
            return pd.concat([raw_df[c], sorted_df], axis=1)
        
    print('No lead found')
    return sorted_df
    
def find_n_cols_groups(df, n_groups=40, stop_thresh=2):
    col_groups = []
    for i in range(n_groups):
        filler = find_filler_value(tmp, i)
        df_view = find_col_order_by_filler(tmp, filler)
        if not all(df_view):
            continue
        for _ in range(stop_thresh + 1):
            df_view = find_leading_col(tmp, df_view)
        col_groups.append(list(df_view.columns))
    return col_groups

def find_bottom_col(raw_df, sorted_df):
    curr_bot = sorted_df.apply(tuple, axis=0).to_frame().rename(columns={0: 'key'}).iloc[-1, 0][:-1]
#     print(curr_bot)
    cols_to_match = raw_df.apply(tuple, axis=0).to_frame().rename(columns={0: 'key'})
    for c in cols_to_match.index:
#         print(cols_to_match.loc[c, 'key'][1:])
        if element_wise_comparison(cols_to_match.loc[c, 'key'][1:], curr_bot, thresh=0):
            print('Bottom col found: {}'.format(c))
            return pd.concat([sorted_df, raw_df.pop(c)], axis=1)
    # In case did not find using thresh=0 set thresh to 1
    for c in cols_to_match.index:
        if element_wise_comparison(cols_to_match.loc[c, 'key'][1:], curr_bot, thresh=1):
            print('Bottom col found: {}'.format(c))
            return pd.concat([sorted_df, raw_df.pop(c)], axis=1)
    
    print('No bottom found')
    return sorted_df

def find_col_order_by_filler_for_ambiguous_cols(df, filler, n_cols=40):
    counts = []
    for c in df.columns:
        v = df[c].values - filler
        counts.append(np.count_nonzero(v))
    counts = np.array(counts)
    args = np.argsort(counts)[::-1]
    stop = np.squeeze(np.where(counts[args] == len(df.index)-2))
    sorted_cols = df.iloc[:, args[stop[0]]].to_frame()
    candidates_pool = df.iloc[:, args[min(stop):]]
    for _ in range(n_cols-2):
        sorted_cols = find_bottom_col(candidates_pool, sorted_cols)

#     return(df.iloc[:, args[stop[0]:]])
    return sorted_cols
#     leaders = np.squeeze(np.where(counts == 0)) # idx of df
#     cols_blocks = []
#     print(leaders)
#     for i, l in enumerate(leaders):
#         print(l)
#         for j in range(n_cols):
#             if not j:
#                 sorted_df = df.iloc[:, l]
#             candidates = np.squeeze(np.where(counts == j+1))
#             candidates_df = df.iloc[:, candidates]
#             print(sorted_df)
#             print(candidates_df)
#             sorted_df = find_leading_col(candidates_df, sorted_df)
#         cols_blocks.append(sorted_df.columns)     
#     return cols_blocks

# def decide_upon_tie(subset_df):
    
# def find_ambiguous_cols_groups(df, ):
#     u, c = np.unique(df.iloc[0,:].values, return_counts=True)
#     arg = np.argsort(c)

In [101]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
tmp = train.loc[rows, :].drop('ID', axis=1)
find_col_order_by_filler_for_ambiguous_cols(tmp, 1032000)
# extra_feats = [find_col_order_by_filler_for_ambiguous_cols(tmp, 1032000)]

Bottom col found: 2d7f256c6
Bottom col found: e98dd91da
Bottom col found: bce33962d
Bottom col found: cdaf3e576
Bottom col found: 78b2cf944
Bottom col found: b3dbb1222
Bottom col found: a2d707f4e
Bottom col found: a5565ec7d
Bottom col found: 26b423c42
Bottom col found: 2731a96a2
Bottom col found: c24634d56
Bottom col found: dc61677e5
Bottom col found: 62c319fd1
Bottom col found: fbe583de5
Bottom col found: ab7534e84
Bottom col found: 92eb376f1
Bottom col found: 7def2d7d3
Bottom col found: 657d07d19
Bottom col found: df08959aa
Bottom col found: 48130b04b
Bottom col found: e0cad27c5
Bottom col found: 0b139c060
Bottom col found: 99df18cb2
Bottom col found: 32c6f9aa6
Bottom col found: 7ff7d351b
Bottom col found: e49fea26e
Bottom col found: 403e7e48d
Bottom col found: c03c8799c
Bottom col found: a3ef40228
Bottom col found: e0ceabad4
Bottom col found: 3c27b0b28
Bottom col found: d833db6e1
Bottom col found: 9303c6806
Bottom col found: 36d35623e
Bottom col found: 208308a47
Bottom col found: 2f

cf4a89033  2d7f256c6  e98dd91da  bce33962d  cdaf3e576  78b2cf944  \
1757    1032000    1032000    1032000    1032000    1032000    1032000   
3809    1032000    1032000    1032000    1032000    1032000    1032000   
511           0    1032000    1032000    1032000    1032000    1032000   
3798          0          0    1032000    1032000    1032000    1032000   
625           0          0          0    1032000    1032000    1032000   
3303     160000          0          0          0    1032000    1032000   
4095          0     160000          0          0          0    1032000   
1283          0          0          0     160000          0          0   
4209          0          0          0          0     160000          0   
1696          0          0          0          0          0     160000   
3511          0          0          0          0          0          0   
816           0          0          0          0          0          0   
245           0          0          0          0          0          0   
1383          0          0          0          0          0          0   
2071          0          0          0          0          0          0   
3492          0          0          0          0          0          0   
378           0          0          0          0          0          0   
2971          0          0          0          0          0          0   
2366          0          0          0          0          0          0   
4414          0          0          0          0          0          0   
2790          0          0          0          0          0          0   
3979          0          0          0          0          0          0   
193           0          0          0          0          0          0   
1189          0          0          0          0          0          0   
3516          0          0          0          0          0          0   
810           0          0          0          0          0          0   
4443          0          0          0          0          0          0   
3697          0          0          0          0          0          0   
235           0          0          0          0          0          0   
1382          0          0          0          0          0          0   
4384          0          0          0          0          0          0   
3418          0          0          0          0          0          0   
4396          0          0          0          0          0          0   
921           0          0          0          0          0          0   
3176          0          0          0          0          0          0   
650           0          0          0          0          0          0   

      b3dbb1222  a2d707f4e  a5565ec7d  26b423c42  2731a96a2  c24634d56  \
1757    1032000    1032000    1032000    1032000    1032000    1032000   
3809    1032000    1032000    1032000    1032000    1032000    1032000   
511     1032000    1032000    1032000    1032000    1032000    1032000   
3798    1032000    1032000    1032000    1032000    1032000    1032000   
625     1032000    1032000    1032000    1032000    1032000    1032000   
3303    1032000    1032000    1032000    1032000    1032000    1032000   
4095    1032000    1032000    1032000    1032000    1032000    1032000   
1283          0    1032000    1032000    1032000    1032000    1032000   
4209          0          0    1032000    1032000    1032000    1032000   
1696          0          0          0    1032000    1032000    1032000   
3511     160000          0          0          0    1032000    1032000   
816           0     160000          0          0          0    1032000   
245           0          0     160000          0          0          0   
1383          0          0          0          0     160000          0   
2071          0          0          0          0          0     160000   
3492          0          0          0          0          0          0   
378      

In [54]:
tmp = train.loc[rows, :].drop('ID', axis=1)
u, c = np.unique(tmp.iloc[0,:].values, return_counts=True)
arg = np.argsort(c)[::-1]
u[arg], c[arg]
# u[np.where(c == 36)]

(array([       0.        ,  1032000.        ,  4000000.        ,
         1500000.        ,  1674000.        ,   662000.        ,
         2000000.        ,  3160000.        ,  3000000.        ,
           80000.        ,  2992315.78      ,  2865694.28      ,
         2831000.        ,  2400000.        , 45138000.        ,
         2202500.        ,  2160000.        ,  2002166.66      ,
         1964666.66      ,   726000.        ,  1775333.34      ,
         3255483.88      ,  1612000.        ,  1563411.76      ,
          210000.        ,  1470000.        ,  1166666.66      ,
         1033000.        ,   400000.        ,   812666.66      ,
          803538.46      ,  3249000.        , 70448000.        ,
         5300000.        ,  4677000.        ,  7822000.        ,
         6902000.        ,  6568857.14      , 11028000.        ,
         5921285.72      ,  5600000.        ,  5422000.        ,
         7440000.        ,  4434140.        , 14650000.        ,
         3822750.        

In [159]:
tmp = test.loc[rows, :].drop('ID', axis=1)
u, c = np.unique(tmp.iloc[0,:].values, return_counts=True)
arg = np.argsort(c)[::-1]
u[arg], c[arg]

(array([       0.        , 43350368.00653622, 11895902.79263306,
         5944923.32203633,  3264389.36821682]),
 array([5028,    1,    1,    1,    1]))

In [102]:
cols = ['f190486d6', '58e2e02e6', 'eeb9cd3aa', '9fd594eec', '6eef030c1', '15ace8c9f', 
        'fb0f5dbfe', '58e056e12', '20aa07010', '024c577b9', 'd6bb78916', 'b43a7cfd5', 
        '58232a6fb', '1702b5bf0', '324921c7b', '62e59a501', '2ec5b290f', '241f0f867', 
        'fb49e4212', '66ace2992', 'f74e8f13d', '5c6487af1', '963a49cdc', '26fc93eb7', 
        '1931ccfdd', '703885424', '70feb1494', '491b9ee45', '23310aa6f', 'e176a204a', 
        '6619d81fc', '1db387535', 
        'fc99f9426',
        '91f701ba2', '0572565c2', '190db8488', 'adb64ff71', 'c47340d97', 'c5a231d81', '0ff32eb98'
       ]
    
# extra_feats = ['ced6a7e91','9df4daa99','83c3779bf','edc84139a','f1e0ada11','73687e512',
#                'aa164b93b','342e7eb03','cd24eae8a','8f3740670','2b2a10857','a00adf70e',
#                '3a48a2cd2','a396ceeb9','9280f3d04','fec5eaf1a','5b943716b','22ed6dba3',
#                '5547d6e11','e222309b0','5d3b81ef8','1184df5c2','2288333b4','f39074b55',
#                'a8b721722','13ee58af1','fb387ea33','4da206d28','ea4046b8d','ef30f6be5',
#                'b85fa8b27','2155f5e16','794e93ca6','070f95c99','939f628a7','7e814a30d',
#                'a6e871369','0dc4d6c7d','bc70cbc26','aca228668']

# extra_feats = [[]]
tmp = train.loc[rows, :].drop('ID', axis=1)
extra_feats = find_n_cols_groups(tmp, 85)
extra_feats

Leading col found: 4e92107c6
Leading col found: 53aa182a2
No lead found
Leading col found: 18562fc62
Leading col found: 81de0d45e
No lead found
Leading col found: d8e951a15
Leading col found: 3391c0af1
No lead found
Leading col found: 9126049d8
Leading col found: a3e023f65
No lead found
Leading col found: ca7ea80a3
Leading col found: ccc7609f4
No lead found
Leading col found: 2b8851e90
Leading col found: 48b839509
No lead found
Leading col found: 34d3715d5
Leading col found: d0d340214
No lead found
Leading col found: 93efdb50f
Leading col found: 920a04ee2
No lead found
Leading col found: c30ff7f31
Leading col found: 0f8d7b98e
No lead found
Leading col found: 9d4428628
No lead found
No lead found
Leading col found: b850c3e18
Leading col found: 5030aed26
No lead found
Leading col found: 9df4daa99
Leading col found: ced6a7e91
No lead found
Leading col found: 36a56d23e
Leading col found: 63be1f619
No lead found
Leading col found: 63c094ba4
Leading col found: 87ffda550
No lead found
Leading

[['53aa182a2',
  '4e92107c6',
  '295408598',
  'b76bf3f19',
  '3305c8063',
  'd3a116347',
  'ac5260727',
  '199caef5d',
  '97ea72529',
  '1d4d5cd4a',
  '8fc7efaf0',
  '225fa9d61',
  '94f3dcaee',
  '4634c8fae',
  '660fdbc58',
  '052f633c1',
  '657dec16b',
  '7fa5bc19f',
  '7207afb67',
  'cda277b2a',
  'e9a473fbb',
  '3eac9a76e',
  '1c554649c',
  '86ffb104c',
  'b14d5014b',
  '8348ea8d3',
  'e3a4596f9',
  '49db469f5',
  'f928893ca',
  'aa610feec',
  'fa2a340da',
  '652142369',
  '947c7c3e8',
  'f81908ca5',
  '8160230fd',
  'c2d200f0e',
  'c99902a93',
  'd3a6362c5',
  '3ee95e3ef',
  '7f8027faf'],
 ['81de0d45e',
  '18562fc62',
  '543c24e33',
  '0256b6714',
  'd6006ff44',
  '6a323434b',
  'e3a38370e',
  '7c444370b',
  '8d2d050a2',
  '9657e51e1',
  '13f3a3d19',
  'b5c839236',
  '70f3033c6',
  'f4b374613',
  '849125d91',
  '16b532cdc',
  '88219c257',
  '74fb8f14c',
  'fd1102929',
  '699712087',
  '22501b58e',
  '9e9274b24',
  '2c42b0dce',
  '2c95e6e31',
  '5263c204d',
  '526ed2bec',
  '01f7de

In [7]:
len(extra_feats)

39

In [78]:

cols_2 = ['ced6a7e91','9df4daa99','83c3779bf','edc84139a','f1e0ada11','73687e512',
                'aa164b93b','342e7eb03','cd24eae8a','8f3740670','2b2a10857','a00adf70e',
                '3a48a2cd2','a396ceeb9','9280f3d04','fec5eaf1a','5b943716b','22ed6dba3',
                '5547d6e11','e222309b0','5d3b81ef8','1184df5c2','2288333b4','f39074b55',
                'a8b721722','13ee58af1','fb387ea33','4da206d28','ea4046b8d','ef30f6be5',
                'b85fa8b27','2155f5e16']
cols = ['f190486d6', '58e2e02e6', 'eeb9cd3aa', '9fd594eec', '6eef030c1', '15ace8c9f', 
        'fb0f5dbfe', '58e056e12', '20aa07010', '024c577b9', 'd6bb78916', 'b43a7cfd5', 
        '58232a6fb', '1702b5bf0', '324921c7b', '62e59a501', '2ec5b290f', '241f0f867', 
        'fb49e4212', '66ace2992', 'f74e8f13d', '5c6487af1', '963a49cdc', '26fc93eb7', 
        '1931ccfdd', '703885424', '70feb1494', '491b9ee45', '23310aa6f', 'e176a204a', 
        '6619d81fc', '1db387535', 
        'fc99f9426',
        '91f701ba2', '0572565c2', '190db8488', 'adb64ff71', 'c47340d97', 'c5a231d81', '0ff32eb98'
       ]
# x = extra_feats

In [7]:
# x = extra_feats
extra_feats = extra_feats[5:]
# del extra_feats[11]

In [36]:
extra_feats

[['ced6a7e91',
  '9df4daa99',
  '83c3779bf',
  'edc84139a',
  'f1e0ada11',
  '73687e512',
  'aa164b93b',
  '342e7eb03',
  'cd24eae8a',
  '8f3740670',
  '2b2a10857',
  'a00adf70e',
  '3a48a2cd2',
  'a396ceeb9',
  '9280f3d04',
  'fec5eaf1a',
  '5b943716b',
  '22ed6dba3',
  '5547d6e11',
  'e222309b0',
  '5d3b81ef8',
  '1184df5c2',
  '2288333b4',
  'f39074b55',
  'a8b721722',
  '13ee58af1',
  'fb387ea33',
  '4da206d28',
  'ea4046b8d',
  'ef30f6be5',
  'b85fa8b27',
  '2155f5e16',
  '794e93ca6',
  '070f95c99',
  '939f628a7',
  '7e814a30d',
  'a6e871369',
  '0dc4d6c7d',
  'bc70cbc26',
  'aca228668']]

In [168]:
extra_feats[13]
extra_feats = [extra_feats[6]]
# extra_feats = [extra_feats[11]]

In [6]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
for i, c in enumerate(extra_feats):
    if not i:
        x = pd.concat([train.loc[rows, ['target']+cols], train.loc[rows, c]], axis=1)
    else:
        x = pd.concat([x, train.loc[rows, c]], axis=1)
# display(train.loc[rows, extra_feats[25]])
display(x)

target    f190486d6    58e2e02e6    eeb9cd3aa    9fd594eec  \
1757    115636.36   1015000.00   1563411.76   1563411.76   1563411.76   
3809    834800.00    540000.00   1015000.00   1563411.76   1563411.76   
511     296444.44    115636.36    540000.00   1015000.00   1563411.76   
3798    247166.66    834800.00    115636.36    540000.00   1015000.00   
625     550000.00    296444.44    834800.00    115636.36    540000.00   
3303   3076666.66    247166.66    296444.44    834800.00    115636.36   
4095    440000.00    550000.00    247166.66    296444.44    834800.00   
1283   1600000.00    440000.00   3076666.66    550000.00    247166.66   
4209    466461.54         0.00    440000.00   3076666.66    550000.00   
1696   3147200.00   1600000.00         0.00    440000.00   3076666.66   
3511     75000.00    466461.54   1600000.00         0.00    440000.00   
816    1586888.88   3147200.00    466461.54   1600000.00         0.00   
245    1477600.00     75000.00   3147200.00    466461.54   1600000.00   
1383    310000.00   1477600.00   1586888.88     75000.00   3147200.00   
2071   3513333.34         0.00   1477600.00   1586888.88     75000.00   
3492    160000.00    310000.00         0.00   1477600.00   1586888.88   
378    2352551.72   3513333.34    310000.00         0.00   1477600.00   
2971    280000.00    160000.00   3513333.34    310000.00         0.00   
2366   5450500.00   2352551.72    160000.00   3513333.34    310000.00   
4414   1359000.00    280000.00   2352551.72    160000.00   3513333.34   
2790     60000.00   5450500.00    280000.00   2352551.72    160000.00   
3979  12000000.00   1359000.00   5450500.00    280000.00   2352551.72   
193     500000.00     60000.00   1359000.00   5450500.00    280000.00   
1189   1878571.42  12000000.00     60000.00   1359000.00   5450500.00   
3516    814800.00    500000.00  12000000.00     60000.00   1359000.00   
810     307000.00   1878571.42    500000.00  12000000.00     60000.00   
4443    528666.66    814800.00   1878571.42    500000.00  12000000.00   
3697    609200.00    307000.00    814800.00   1878571.42    500000.00   
235     406000.00    528666.66    307000.00    814800.00   1878571.42   
1382    448666.66    609200.00    528666.66    307000.00    814800.00   
4384    400000.00    448666.66    406000.00    609200.00    528666.66   
3418     60666.66         0.00    448666.66    406000.00    609200.00   
4396    267428.58    400000.00         0.00    448666.66    406000.00   
921    1304800.00     60666.66    400000.00         0.00    448666.66   
3176   8120000.00    267428.58     60666.66    400000.00         0.00   
650     380000.00   1304800.00    267428.58     60666.66    400000.00   

        6eef030c1    15ace8c9f    fb0f5dbfe   58e056e12    20aa07010  \
1757   1563411.76   1563411.76   1563411.76  1563411.76   1563411.76   
3809   1563411.76   1563411.76   1563411.76  1563411.76   1563411.76   
511    1563411.76   1563411.76   1563411.76  1563411.76   1563411.76   
3798   1563411.76   1563411.76   1563411.76  1563411.76   1563411.76   
625    1015000.00   1563411.76   1563411.76  1563411.76   1563411.76   
3303    540000.00   1015000.00   1563411.76  1563411.76   1563411.76   
4095    115636.36    540000.00   1015000.00  1563411.76   1563411.76   
1283    296444.44    834800.00    115636.36   540000.00   1015000.00   
4209    247166.66    296444.44    834800.00   115636.36    540000.00   
1696    550000.00    247166.66    296444.44   834800.00    115636.36   
3511   3076666.66    550000.00    247166.66   296444.44    834800.00   
816     440000.00   3076666.66    550000.00   247166.66    296444.44   
245          0.00    440000.00   3076666.66   550000.00    247166.66   
1383    466461.54   1600000.00         0.00   440000.00   3076666.66   
2071   3147200.00    466461.54   1600000.00        0.00    440000.00   
3492     75000.00   3147200.00    466461.54  1600000.00         0.00   
378    1586888.88     75000.00   3147200.00   466461.54   1600000.00   
2971   147760

# Find leaks

In [103]:
# from: https://www.kaggle.com/dfrumkin/a-simple-way-to-use-giba-s-features-v2
def _get_leak(df, cols, extra_feats=[[]], lag=0):
    f1 = cols[:-lag-2]
    f2 = cols[lag+2:]
    for ef in extra_feats:
        f1 += ef[:-lag-2]
        f2 += ef[lag+2:]
    
    
    d1 = df[f1].apply(tuple, axis=1).to_frame().rename(columns={0: 'key'})
    d2 = df[f2].apply(tuple, axis=1).to_frame().rename(columns={0: 'key'})
    d2['pred'] = df[cols[lag]]
    #d2 = d2[d2.pred != 0] ### to make output consistent with Hasan's function
    d3 = d2[~d2.duplicated(['key'], keep=False)]
    return d1.merge(d3, how='left', on='key').pred.fillna(0)

In [104]:
def compiled_leak_result(extra_cols, verbose=True):    
    max_nlags = len(cols) - 2
    train_leak = train
    train_leak["compiled_leak"] = 0
    train_leak["nonzero_mean"] = train[transact_cols].apply(
        lambda x: np.expm1(np.log1p(x[x!=0]).mean()), axis=1
    )
    
    scores = []
    leaky_value_counts = []
    leaky_value_corrects = []
    leaky_cols = []
    
    for i in range(max_nlags):
        c = "leaked_target_"+str(i)
        if verbose:
            print('Processing lag', i)
        train_leak[c] = _get_leak(train_leak, cols, extra_cols, i)
        
        leaky_cols.append(c)
#         train_leak = train.join(train_leak[leaky_cols+["compiled_leak", "nonzero_mean", "ID"]], on='ID', how='left')
        zeroleak = train_leak["compiled_leak"]==0
        train_leak.loc[zeroleak, "compiled_leak"] = train_leak.loc[zeroleak, c]
        leaky_value_counts.append(sum(train_leak["compiled_leak"] > 0))
        _correct_counts = sum(train_leak["compiled_leak"]==train_leak["target"])
        leaky_value_corrects.append(_correct_counts/leaky_value_counts[-1])
        if verbose:
            print("Leak values found in train", leaky_value_counts[-1])
            print(
                "% of correct leaks values in train ", 
                leaky_value_corrects[-1])
        tmp = train_leak.copy()
        tmp.loc[zeroleak, "compiled_leak"] = train_leak["nonzero_mean"]
        scores.append(np.sqrt(mean_squared_error(y, np.log1p(tmp["compiled_leak"]).fillna(14.49))))
        if verbose:
            print(
                'Score (filled with nonzero mean)', 
                scores[-1])
        gc.collect()
    result = dict(
        score=scores, 
        leaky_count=leaky_value_counts,
        leaky_correct=leaky_value_corrects,
    )
    return train_leak, result

# Find helpful cols

In [105]:
good_cols = []
_, result = compiled_leak_result([[]], verbose=False)
ref = min(result['score'])
for i in range(len(extra_feats)):
    extra_cols = [extra_feats[i]]
    _, result = compiled_leak_result(extra_cols, verbose=False)
    if min(result['score']) < ref:
        print('Good col found, leader is ', extra_feats[i][0])
        good_cols.append(extra_feats[i])
print(len(good_cols), ' good columns found!')

Good col found, leader is  81de0d45e
Good col found, leader is  a3e023f65
Good col found, leader is  ccc7609f4
Good col found, leader is  48b839509
Good col found, leader is  d0d340214
Good col found, leader is  920a04ee2
Good col found, leader is  0f8d7b98e
Good col found, leader is  9d4428628
Good col found, leader is  5030aed26
Good col found, leader is  ced6a7e91
Good col found, leader is  63be1f619
Good col found, leader is  87ffda550
Good col found, leader is  1d9078f84
Good col found, leader is  2135fa05a
Good col found, leader is  f3cf9341c
Good col found, leader is  c928b4b74
Good col found, leader is  51c141e64
Good col found, leader is  1ad24da13
Good col found, leader is  4302b67ec
Good col found, leader is  b6daeae32
Good col found, leader is  fec5644cf
Good col found, leader is  7f72c937f
Good col found, leader is  5b465f819
Good col found, leader is  df838756c
Good col found, leader is  266525925
Good col found, leader is  c13ee1dc9
Good col found, leader is  a1cd7b681
G

In [106]:
train_leak, result = compiled_leak_result(good_cols)
# train_leak, result = compiled_leak_result(extra_feats)

Processing lag 0
Leak values found in train 1388
% of correct leaks values in train  1.0
Score (filled with nonzero mean) 1.5138333391635181
Processing lag 1
Leak values found in train 2010
% of correct leaks values in train  1.0
Score (filled with nonzero mean) 1.2798076584961116
Processing lag 2
Leak values found in train 2407
% of correct leaks values in train  0.9995845450768591
Score (filled with nonzero mean) 1.147271682194531
Processing lag 3
Leak values found in train 2667
% of correct leaks values in train  0.9996250468691413
Score (filled with nonzero mean) 1.0476286768564789
Processing lag 4
Leak values found in train 2840
% of correct leaks values in train  0.9996478873239436
Score (filled with nonzero mean) 0.9891066336923242
Processing lag 5
Leak values found in train 2993
% of correct leaks values in train  0.9996658870698296
Score (filled with nonzero mean) 0.9486940499678514
Processing lag 6
Leak values found in train 3115
% of correct leaks values in train  0.99967897

In [107]:
result = pd.DataFrame.from_dict(result, orient='columns')
result.T

0            1            2            3   \
leaky_correct     1.000000     1.000000     0.999585     0.999625   
leaky_count    1388.000000  2010.000000  2407.000000  2667.000000   
score             1.513833     1.279808     1.147272     1.047629   

                        4            5            6            7   \
leaky_correct     0.999648     0.999666     0.999679     0.999689   
leaky_count    2840.000000  2993.000000  3115.000000  3217.000000   
score             0.989107     0.948694     0.899494     0.851132   

                        8            9            10           11  \
leaky_correct     0.999697     0.999702     0.999708     0.999711   
leaky_count    3303.000000  3357.000000  3420.000000  3464.000000   
score             0.820565     0.800645     0.786025     0.770757   

                        12           13           14           15  \
leaky_correct     0.999715     0.999719     0.999722     0.999724   
leaky_count    3510.000000  3556.000000  3596.000000  3625.000000   
score             0.752834     0.737395     0.719612     0.704213   

                        16           17           18           19  \
leaky_correct     0.999726     0.999728     0.999729     0.999730   
leaky_count    3645.000000  3670.000000  3691.000000  3710.000000   
score             0.694713     0.685599     0.675677     0.666122   

                        20           21           22           23  \
leaky_correct     0.999732     0.999733     0.999734     0.999735   
leaky_count    3725.000000  3743.000000  3758.000000  3775.000000   
score             0.655324     0.643108     0.633261     0.628552   

                        24           25           26           27  \
leaky_correct     0.999736     0.999737     0.999737     0.999476   
leaky_count    3788.000000  3796.000000  3808.000000  3816.000000   
score             0.621282     0.619423     0.617082     0.610226   

                        28           29           30           31  \
leaky_correct     0.999477     0.999478     0.999478     0.999218   
leaky_count    3822.000000  3828.000000  3834.000000  3838.000000   
score             0.604919     0.602805     0.599573     0.597415   

                        32           33           34           35  \
leaky_correct     0.998959     0.998962     0.998704     0.998188   
leaky_count    3844.000000  3853.000000  3859.000000  3864.000000   
score             0.596461     0.594082     0.589793     0.588767   

                        36           37  
leaky_correct     0.997672     0.997415  
leaky_count    3866.000000  3869.000000  
score             0.585366     0.585602

In [108]:
result.to_csv('train_leaky_stat.csv', index=False)

In [109]:
train_leak.head()

ID      target  48df886f9  0deb4b6a8  34b15f335  a8cb14b00  \
0  000d6aaf2  38000000.0        0.0          0        0.0          0   
1  000fbd867    600000.0        0.0          0        0.0          0   
2  0027d6b71  10000000.0        0.0          0        0.0          0   
3  0028cbf45   2000000.0        0.0          0        0.0          0   
4  002a68644  14400000.0        0.0          0        0.0          0   

   2f0771a37  30347e683  d08d1fbe3  6ee66e115  20aa07010  dc5a8f1d8  \
0          0          0          0          0        0.0        0.0   
1          0          0          0          0  2200000.0        0.0   
2          0          0          0          0        0.0        0.0   
3          0          0          0          0        0.0        0.0   
4          0          0          0          0  2000000.0        0.0   

   11d86fa6a  77c9823f2  8d6c2a0b2  4681de4fd  adf119b9a  cff75dd09  \
0        0.0          0          0          0          0        0.0   
1        0.0          0          0          0          0        0.0   
2        0.0          0          0          0          0        0.0   
3        0.0          0          0          0          0        0.0   
4        0.0          0          0          0          0        0.0   

   96f83a237  b8a716ebf  6c7a4567c  4fcfd2b4d  f3b9c0b95  71cebf11c  \
0          0        0.0          0          0        0.0          0   
1          0        0.0          0          0        0.0          0   
2          0        0.0          0          0        0.0          0   
3          0        0.0          0          0        0.0          0   
4          0        0.0          0          0        0.0          0   

   d966ac62c  68b647452  c88d108c9  ff7b471cd  d5308d8bc  0d866c3d7  \
0          0        0.0          0          0          0        0.0   
1          0        0.0          0          0          0        0.0   
2          0        0.0          0          0          0        0.0   
3          0        0.0          0          0          0        0.0   
4          0        0.0          0          0          0        0.0   

   bc3f77679  bd8f989f1  0eff5bf95  22ed6dba3  92b13ebba  c330f1a67  \
0          0        0.0          0        0.0        0.0          0   
1          0        0.0          0        0.0        0.0          0   
2          0        0.0          0        0.0        0.0          0   
3          0        0.0          0        0.0        0.0          0   
4          0        0.0          0        0.0        0.0          0   

   233c7c17c  2cb4d123e  eeac16933  87ffda550  822e49b95  316b978cd  \
0        0.0          0          0  1300000.0        0.0          0   
1        0.0          0          0        0.0        0.0          0   
2        0.0          0          0        0.0        0.0          0   
3        0.0          0          0        0.0        0.0          0   
4        0.0          0          0        0.0        0.0          0   

   d04e16aed  5d5c5ce6d  ec863cb52  11ad148bd  ea18d720e  408d86ce9  \
0        0.0          0          0        0.0        0.0        0.0   
1        0.0          0          0        0.0        0.0        0.0   
2        0.0          0          0        0.0        0.0        0.0   
3        0.0          0          0        0.0        0.0        0.0   
4        0.0          0          0        0.0        0.0        0.0   

   69d8b4020  b0868a049  80b14398e  ecdef52b2  c36bcacc5  151d318cd  \
0          0          0        0.0        0.0          0          0   
1          0          0        0.0        0.0          0          0   
2          0          0        0.0        0.0          0          0   
3          0          0        0.0        0.0          0          0   
4          0          0        0.0        0.0          0          0   

   ab0cddb90  2d6bd8275   dfdf4b580  c87722678  a8c320153  7df8788e8  \
0          0        0.0         0.0          0          0          0   
1          0     

In [110]:
best_score = np.min(result['score'])
best_lag = np.argmin(result['score'])
print('best_score', best_score, '\nbest_lag', best_lag)

best_score 0.5853656708265186 
best_lag 36


In [111]:
def rewrite_compiled_leak(leak_df, lag):
    leak_df["compiled_leak"] = 0
    for i in range(lag):
        c = "leaked_target_"+str(i)
        zeroleak = leak_df["compiled_leak"]==0
        leak_df.loc[zeroleak, "compiled_leak"] = leak_df.loc[zeroleak, c]
    return leak_df

In [112]:
leaky_cols = [c for c in train_leak.columns if 'leaked_target_' in c]
train_leak = rewrite_compiled_leak(train_leak, best_lag)
train_leak[['ID']+leaky_cols+['compiled_leak']].head()

ID  leaked_target_0  leaked_target_1  leaked_target_2  \
0  000d6aaf2       38000000.0       38000000.0       38000000.0   
1  000fbd867         600000.0              0.0              0.0   
2  0027d6b71              0.0              0.0              0.0   
3  0028cbf45              0.0              0.0              0.0   
4  002a68644              0.0              0.0              0.0   

   leaked_target_3  leaked_target_4  leaked_target_5  leaked_target_6  \
0              0.0       38000000.0              0.0       38000000.0   
1              0.0              0.0              0.0         600000.0   
2              0.0              0.0              0.0              0.0   
3        2000000.0              0.0              0.0              0.0   
4              0.0              0.0              0.0              0.0   

   leaked_target_7  leaked_target_8  leaked_target_9  leaked_target_10  \
0              0.0              0.0              0.0        38000000.0   
1              0.0         600000.0              0.0               0.0   
2              0.0              0.0              0.0               0.0   
3              0.0              0.0              0.0               0.0   
4              0.0              0.0              0.0               0.0   

   leaked_target_11  leaked_target_12  leaked_target_13  leaked_target_14  \
0        38000000.0               0.0        38000000.0        38000000.0   
1          600000.0               0.0               0.0               0.0   
2               0.0               0.0               0.0               0.0   
3               0.0               0.0               0.0               0.0   
4               0.0               0.0               0.0               0.0   

   leaked_target_15  leaked_target_16  leaked_target_17  leaked_target_18  \
0               0.0               0.0        38000000.0               0.0   
1          600000.0               0.0               0.0               0.0   
2               0.0               0.0               0.0               0.0   
3               0.0               0.0               0.0               0.0   
4               0.0               0.0               0.0               0.0   

   leaked_target_19  leaked_target_20  leaked_target_21  leaked_target_22  \
0        38000000.0               0.0               0.0               0.0   
1               0.0               0.0               0.0               0.0   
2               0.0               0.0               0.0               0.0   
3               0.0               0.0               0.0               0.0   
4               0.0               0.0               0.0               0.0   

   leaked_target_23  leaked_target_24  leaked_target_25  leaked_target_26  \
0               0.0               0.0        38000000.0               0.0   
1               0.0               0.0          600000.0               0.0   
2               0.0               0.0               0.0               0.0   
3               0.0               0.0               0.0         2000000.0   
4               0.0               0.0               0.0               0.0   

   leaked_target_27  leaked_target_28  leaked_target_29  leaked_target_30  \
0        38000000.0               0.0        38000000.0               0.0   
1               0.0               0.0               0.0               0.0   
2               0.0               0.0               0.0               0.0   
3               0.0               0.0               0.0               0.0   
4               0.0               0.0               0.0               0.0   

   leaked_target_31  leaked_target_32  leaked_target_33  leaked_target_34  \
0        38000000.0               0.0        38000000.0        38000000.0   
1               0.0               0.0               0.0               0.0   
2               0.0               0.0               0.0               0.0   
3         2000000.0               0.0               0.0               0.0   
4               0.0    

In [113]:
train_res = train_leak[leaky_cols+['compiled_leak']].replace(0.0, np.nan)
train_res.to_csv('train_leak.csv', index=False)

In [118]:
def compiled_leak_result_test(max_nlags, extra_cols):
    test_leak = test
    test_leak["compiled_leak"] = 0
    test_leak["nonzero_mean"] = test[transact_cols].apply(
        lambda x: np.expm1(np.log1p(x[x!=0]).mean()), axis=1
    )
    
    scores = []
    leaky_value_counts = []
    # leaky_value_corrects = []
    leaky_cols = []
    
    for i in range(max_nlags):
        c = "leaked_target_"+str(i)
        
        print('Processing lag', i)
        test_leak[c] = _get_leak(test_leak, cols, extra_cols, i)
        
        leaky_cols.append(c)
#         test_leak = test.join(
#             test_leak.set_index("ID")[leaky_cols+["compiled_leak", "nonzero_mean"]], 
#             on="ID", how="left"
#         )[["ID", "target"] + cols + leaky_cols+["compiled_leak", "nonzero_mean"]]
        zeroleak = test_leak["compiled_leak"]==0
        test_leak.loc[zeroleak, "compiled_leak"] = test_leak.loc[zeroleak, c]
        leaky_value_counts.append(sum(test_leak["compiled_leak"] > 0))
        #_correct_counts = sum(train_leak["compiled_leak"]==train_leak["target"])
        #leaky_value_corrects.append(_correct_counts/leaky_value_counts[-1])
        print("Leak values found in test", leaky_value_counts[-1])
        #print(
        #    "% of correct leaks values in train ", 
        #    leaky_value_corrects[-1]
        #)
        #tmp = train_leak.copy()
        #tmp.loc[zeroleak, "compiled_leak"] = tmp.loc[zeroleak, "nonzero_mean"]
        #scores.append(np.sqrt(mean_squared_error(y, np.log1p(tmp["compiled_leak"]).fillna(14.49))))
        #print(
        #    'Score (filled with nonzero mean)', 
        #    scores[-1]
        #)
    result = dict(
        # score=scores, 
        leaky_count=leaky_value_counts,
        # leaky_correct=leaky_value_corrects,
    )
    return test_leak, result

In [140]:
test_leak, test_result = compiled_leak_result_test(38, extra_cols)

Processing lag 0
Leak values found in test 2965
Processing lag 1
Leak values found in test 4219
Processing lag 2
Leak values found in test 4961
Processing lag 3
Leak values found in test 5514
Processing lag 4
Leak values found in test 5935
Processing lag 5
Leak values found in test 6229
Processing lag 6
Leak values found in test 6439
Processing lag 7
Leak values found in test 6597
Processing lag 8
Leak values found in test 6756
Processing lag 9
Leak values found in test 6893
Processing lag 10
Leak values found in test 7006
Processing lag 11
Leak values found in test 7101
Processing lag 12
Leak values found in test 7179
Processing lag 13
Leak values found in test 7260
Processing lag 14
Leak values found in test 7322
Processing lag 15
Leak values found in test 7382
Processing lag 16
Leak values found in test 7437
Processing lag 17
Leak values found in test 7476
Processing lag 18
Leak values found in test 7512
Processing lag 19
Leak values found in test 7554
Processing lag 20
Leak values 

In [141]:
test_result = pd.DataFrame.from_dict(test_result, orient='columns')
test_result.T

0     1     2     3     4     5     6     7     8     9     10  \
leaky_count  2965  4219  4961  5514  5935  6229  6439  6597  6756  6893  7006   

               11    12    13    14    15    16    17    18    19    20    21  \
leaky_count  7101  7179  7260  7322  7382  7437  7476  7512  7554  7600  7630   

               22    23    24    25    26    27    28    29    30    31    32  \
leaky_count  7671  7697  7720  7741  7760  7787  7817  7869  7916  7975  8058   

               33    34    35    36    37  
leaky_count  8185  8371  8559  8884  9372

In [142]:
test_result.to_csv('test_leaky_stat.csv', index=False)

In [149]:
test_leak = rewrite_compiled_leak(test_leak, 29)
test_leak[['ID']+leaky_cols+['compiled_leak']].head()

ID  leaked_target_0  leaked_target_1  leaked_target_2  \
0  000137c73              0.0              0.0              0.0   
1  00021489f              0.0              0.0              0.0   
2  0004d7953              0.0              0.0              0.0   
3  00056a333              0.0              0.0              0.0   
4  00056d8eb              0.0              0.0              0.0   

   leaked_target_3  leaked_target_4  leaked_target_5  leaked_target_6  \
0              0.0              0.0              0.0              0.0   
1              0.0              0.0              0.0              0.0   
2              0.0              0.0              0.0              0.0   
3              0.0              0.0              0.0              0.0   
4              0.0              0.0              0.0              0.0   

   leaked_target_7  leaked_target_8  leaked_target_9  leaked_target_10  \
0              0.0              0.0              0.0               0.0   
1              0.0              0.0              0.0               0.0   
2              0.0              0.0              0.0               0.0   
3              0.0              0.0              0.0               0.0   
4              0.0              0.0              0.0               0.0   

   leaked_target_11  leaked_target_12  leaked_target_13  leaked_target_14  \
0               0.0               0.0               0.0               0.0   
1               0.0               0.0               0.0               0.0   
2               0.0               0.0               0.0               0.0   
3               0.0               0.0               0.0               0.0   
4               0.0               0.0               0.0               0.0   

   leaked_target_15  leaked_target_16  leaked_target_17  leaked_target_18  \
0               0.0               0.0               0.0               0.0   
1               0.0               0.0               0.0               0.0   
2               0.0               0.0               0.0               0.0   
3               0.0               0.0               0.0               0.0   
4               0.0               0.0               0.0               0.0   

   leaked_target_19  leaked_target_20  leaked_target_21  leaked_target_22  \
0               0.0               0.0               0.0               0.0   
1               0.0               0.0               0.0               0.0   
2               0.0               0.0               0.0               0.0   
3               0.0               0.0               0.0               0.0   
4               0.0               0.0               0.0               0.0   

   leaked_target_23  leaked_target_24  leaked_target_25  leaked_target_26  \
0               0.0               0.0               0.0               0.0   
1               0.0               0.0               0.0               0.0   
2               0.0               0.0               0.0               0.0   
3               0.0               0.0               0.0               0.0   
4               0.0               0.0               0.0               0.0   

   leaked_target_27  leaked_target_28  leaked_target_29  leaked_target_30  \
0               0.0               0.0               0.0               0.0   
1               0.0               0.0               0.0               0.0   
2               0.0               0.0               0.0               0.0   
3               0.0               0.0               0.0               0.0   
4               0.0               0.0               0.0               0.0   

   leaked_target_31  leaked_target_32  leaked_target_33  leaked_target_34  \
0               0.0               0.0               0.0               0.0   
1               0.0               0.0               0.0               0.0   
2               0.0               0.0               0.0               0.0   
3               0.0               0.0               0.0               0.0   
4               0.0    

In [145]:
test_res = test_leak[leaky_cols+['compiled_leak']].replace(0.0, np.nan)
test_res.to_csv('test_leak.csv', index=False)

In [146]:
# test_leak.loc[test_leak["compiled_leak"]==0, "compiled_leak"] = test_leak.loc[test_leak["compiled_leak"]==0, "nonzero_mean"]
test_leak.loc[test_leak["compiled_leak"]==0, "compiled_leak"] = 0

In [150]:
#submission
sub = test[["ID"]]
sub["target"] = test_leak["compiled_leak"]
sub.to_csv(f"baseline_sub_lag_{best_lag}.csv", index=False)
print(f"baseline_sub_lag_{best_lag}.csv saved")

baseline_sub_lag_36.csv saved


In [ ]:
sub.head()

In [151]:
# Mix with other pred
sub_no_leak = pd.read_csv('sub_138.csv')
ensemble_sub = sub
ensemble_sub[sub['target'] == 0] = sub_no_leak[sub['target'] == 0]
ensemble_sub.to_csv(f"submission1.csv", index=False)
print(f"ensemble saved")

ensemble saved
